In [144]:
import pandas as pd
import numpy as np

df = pd.read_csv(r"C:\Users\William Prawira\Documents\GitHub\olympic-swimming\data\Olympic_Swimming_Results_1912to2020.csv")

df

Location  Year Distance (in meters)             Stroke  Relay? Gender  \
0         Tokyo  2020                 100m         Backstroke       0    Men   
1         Tokyo  2020                 100m         Backstroke       0    Men   
2         Tokyo  2020                 100m         Backstroke       0    Men   
3         Tokyo  2020                 100m         Backstroke       0    Men   
4         Tokyo  2020                 100m         Backstroke       0    Men   
5         Tokyo  2020                 100m         Backstroke       0    Men   
6         Tokyo  2020                 100m         Backstroke       0    Men   
7         Tokyo  2020                 100m         Backstroke       0    Men   
8         Tokyo  2020                 100m       Breaststroke       0    Men   
9         Tokyo  2020                 100m       Breaststroke       0    Men   
10        Tokyo  2020                 100m       Breaststroke       0    Men   
11        Tokyo  2020                 100m       Breaststroke       0    Men   
12        Tokyo  2020                 100m       Breaststroke       0    Men   
13        Tokyo  2020                 100m       Breaststroke       0    Men   
14        Tokyo  2020                 100m       Breaststroke       0    Men   
15        Tokyo  2020                 100m       Breaststroke       0    Men   
16        Tokyo  2020                 100m          Butterfly       0    Men   
17        Tokyo  2020                 100m          Butterfly       0    Men   
18        Tokyo  2020                 100m          Butterfly       0    Men   
19        Tokyo  2020                 100m          Butterfly       0    Men   
20        Tokyo  2020                 100m          Butterfly       0    Men   
21        Tokyo  2020                 100m          Butterfly       0    Men   
22        Tokyo  2020                 100m          Butterfly       0    Men   
23        Tokyo  2020                 100m          Butterfly       0    Men   
24        Tokyo  2020                 100m          Freestyle       0    Men   
25        Tokyo  2020                 100m          Freestyle       0    Men   
26        Tokyo  2020                 100m          Freestyle       0    Men   
27        Tokyo  2020                 100m          Freestyle       0    Men   
28        Tokyo  2020                 100m          Freestyle       0    Men   
29        Tokyo  2020                 100m          Freestyle       0    Men   
30        Tokyo  2020                 100m          Freestyle       0    Men   
31        Tokyo  2020                 100m          Freestyle       0    Men   
32        Tokyo  2020                1500m          Freestyle       0    Men   
33        Tokyo  2020                1500m          Freestyle       0    Men   
34        Tokyo  2020                1500m          Freestyle       0    Men   
35        Tokyo  2020                1500m          Freestyle       0    Men   
36        Tokyo  2020                1500m          Freestyle       0    Men   
37        Tokyo  2020                1500m          Freestyle       0    Men   
38        Tokyo  2020                1500m          Freestyle       0    Men   
39        Tokyo  2020                1500m          Freestyle       0    Men   
40        Tokyo  2020                 200m         Backstroke       0    Men   
41        Tokyo  2020                 200m         Backstroke       0    Men   
42        Tokyo  2020                 200m         Backstroke       0    Men   
43        Tokyo  2020                 200m         Backstroke       0    Men   
44        Tokyo  2020                 200m         Backstroke       0    Men   
45        Tokyo  2020                 200m         Backstroke       0    Men   
46        Tokyo  2020                 200m         Backstroke       0    Men   
47        Tokyo  2020                 200m         Backstroke       0    Men   
48        Tokyo  2020                 200m       Breaststroke       0    Men   
49     

Basic EDA

In [145]:
df.isnull().sum()

Location                 0
Year                     0
Distance (in meters)     0
Stroke                   0
Relay?                   0
Gender                   0
Team                     0
Athlete                 14
Results                 28
Rank                     0
dtype: int64

In [146]:
df.describe()

Year       Relay?         Rank
count  4359.000000  4359.000000  4359.000000
mean   1982.936453     0.169764     3.164946
std      26.928344     0.375468     1.189715
min    1912.000000     0.000000     0.000000
25%    1968.000000     0.000000     2.000000
50%    1988.000000     0.000000     4.000000
75%    2004.000000     0.000000     4.000000
max    2020.000000     1.000000     5.000000

In [147]:
df.dtypes

Location                object
Year                     int64
Distance (in meters)    object
Stroke                  object
Relay?                   int64
Gender                  object
Team                    object
Athlete                 object
Results                 object
Rank                     int64
dtype: object

In [148]:
df = df[df['Relay?'] == 0]
df = df.drop(columns=["Location"])
df["Event"] = df["Distance (in meters)"].astype(str) + " " + df["Stroke"]
df = df.drop(columns=["Distance (in meters)", "Stroke", "Relay?"])

cols = df.columns.tolist()
cols.insert(cols.index("Year") + 1, cols.pop(cols.index("Event")))
df = df[cols]

df = df.dropna()
df = df[df["Results"].str.lower() != "did not finish"]

df = df.reset_index(drop=True)

In [149]:
def parse_swim_time(x):
    """Convert messy swim times into total seconds (float)."""
    s = str(x).strip()

    # Case 1: plain numbers like 51.98, 52, 52.123
    try:
        return float(s)
    except ValueError:
        pass
    
    # Case 2: colon-separated formats (m:ss.ms, mm:ss.ms, hh:mm:ss.msssss)
    parts = s.split(":")
    try:
        parts = [float(p) for p in parts]
        if len(parts) == 3: # hh:mm:ss.ms
            h, m, sec = parts
            return h*3600 + m*60 + sec
        elif len(parts) == 2: # mm:ss.ms or m:ss.ms
            m, sec = parts
            return m*60 + sec
    except:
        return None
    
    return None

def format_mm_ss_ms(sec):
    """Convert seconds into mm:ss.ms format (standard style)"""
    minutes = int(sec // 60)
    seconds = sec % 60
    return f"{minutes:02d}:{seconds:05.2f}"

# Apply to dataframe
df["Results_seconds"] = df["Results"].apply(parse_swim_time)
df = df.dropna(subset=["Results_seconds"]) # Remove bad rows
df["Results"] = df["Results_seconds"].apply(format_mm_ss_ms)

In [150]:
df

Year                   Event Gender Team  \
0     2020         100m Backstroke    Men  ROC   
1     2020         100m Backstroke    Men  ROC   
2     2020         100m Backstroke    Men  USA   
3     2020         100m Backstroke    Men  ITA   
4     2020         100m Backstroke    Men  CHN   
5     2020         100m Backstroke    Men  ESP   
6     2020         100m Backstroke    Men  AUS   
7     2020         100m Backstroke    Men  ROU   
8     2020       100m Breaststroke    Men  GBR   
9     2020       100m Breaststroke    Men  NED   
10    2020       100m Breaststroke    Men  ITA   
11    2020       100m Breaststroke    Men  USA   
12    2020       100m Breaststroke    Men  GBR   
13    2020       100m Breaststroke    Men  CHN   
14    2020       100m Breaststroke    Men  USA   
15    2020       100m Breaststroke    Men  BLR   
16    2020          100m Butterfly    Men  USA   
17    2020          100m Butterfly    Men  HUN   
18    2020          100m Butterfly    Men  SUI   
19    2020          100m Butterfly    Men  ROC   
20    2020          100m Butterfly    Men  POL   
21    2020          100m Butterfly    Men  AUS   
22    2020          100m Butterfly    Men  GUA   
23    2020          100m Butterfly    Men  BUL   
24    2020          100m Freestyle    Men  USA   
25    2020          100m Freestyle    Men  AUS   
26    2020          100m Freestyle    Men  ROC   
27    2020          100m Freestyle    Men  FRA   
28    2020          100m Freestyle    Men  KOR   
29    2020          100m Freestyle    Men  ITA   
30    2020          100m Freestyle    Men  ROU   
31    2020          100m Freestyle    Men  HUN   
32    2020         1500m Freestyle    Men  USA   
33    2020         1500m Freestyle    Men  UKR   
34    2020         1500m Freestyle    Men  GER   
35    2020         1500m Freestyle    Men  ITA   
36    2020         1500m Freestyle    Men  GBR   
37    2020         1500m Freestyle    Men  ROC   
38    2020         1500m Freestyle    Men  AUT   
39    2020         1500m Freestyle    Men  UKR   
40    2020         200m Backstroke    Men  ROC   
41    2020         200m Backstroke    Men  USA   
42    2020         200m Backstroke    Men  GBR   
43    2020         200m Backstroke    Men  USA   
44    2020         200m Backstroke    Men  HUN   
45    2020         200m Backstroke    Men  POL   
46    2020         200m Backstroke    Men  JPN   
47    2020         200m Backstroke    Men  ESP   
48    2020       200m Breaststroke    Men  AUS   
49    2020       200m Breaststroke    Men  NED   
50    2020       200m Breaststroke    Men  FIN   
51    2020       200m Breaststroke    Men  ROC   
52    2020       200m Breaststroke    Men  USA   
53    2020       200m Breaststroke    Men  GBR   
54    2020       200m Breaststroke    Men  JPN   
55    2020       200m Breaststroke    Men  SWE   
56    2020          200m Butterfly    Men  HUN   
57    2020          200m Butterfly    Men  JPN   
58    2020          200m Butterfly    Men  ITA   
59    2020          200m Butterfly    Men  HUN   
60    2020          200m Butterfly    Men  RSA   
61    2020          200m Butterfly    Men  BRA   
62    2020          200m Butterfly    Men  USA   
63    2020          200m Butterfly    Men  POL   
64    2020          200m Freestyle    Men  GBR   
65    2020          200m Freestyle    Men  GBR   
66    2020          200m Freestyle    Men  BRA   
67    2020          200m Freestyle    Men  ROU   
68    2020          200m Freestyle    Men  ROC   
69    2020          200m Freestyle    Men  USA   
70    2020          200m Freestyle    Men  KOR   
71    2020          200m Freestyle    Men  LTU   
72    2020  200m Individual medley    Men  CHN   
73    2020  200m Individual medley    Men  GBR   
74    2020  200m Individual medley    Men  SUI   
75    2020  200m Individual medley    Men  JPN   
76    2020  200m Individual medley    Men  USA   
77    2020  200m Individual medley    Men  JPN   
78    2020  200m Individual medley    Men  HUN   
79    

In [151]:
df["Year"].dtype

dtype('int64')

In [152]:
df["Year"] = pd.to_datetime(df["Year"].astype(str), format="%Y")
df["Year"] = df["Year"].dt.to_period("Y")

df["Year"].dtype

period[Y-DEC]

In [153]:
summary = (
    df.groupby(["Year", "Event", "Gender"])["Results_seconds"]
      .mean()
      .reset_index()
      .rename(columns={"Results_seconds": "Avg_Results_seconds"})
)
summary["Avg_Results"] = summary["Avg_Results_seconds"].apply(format_mm_ss_ms)

summary.to_csv("event_year_summary.txt", sep='\t', index=False)